In [37]:
!pip install --upgrade pip setuptools wheel

Please see https://github.com/pypa/pip/issues/5599 for advice on fixing the underlying issue.
To avoid this problem you can invoke Python with '-m pip' instead of running pip directly.


In [38]:
!pip install p5py PEP517 pymongo pandas

Please see https://github.com/pypa/pip/issues/5599 for advice on fixing the underlying issue.
To avoid this problem you can invoke Python with '-m pip' instead of running pip directly.


In [39]:
from pymongo import MongoClient
import pandas as pd

In [40]:
client = MongoClient("mongodb://localhost")
client

MongoClient(host=['localhost:27017'], document_class=dict, tz_aware=False, connect=True)

In [41]:
client.list_database_names()

['admin', 'config', 'local']

In [42]:
db = client.network_report

In [43]:
db.list_collection_names()

[]

In [44]:
c = db['exfo_api'].find()
len(list(c))

0

In [ ]:
all_result = list(db['exfo_api'].find({'ids.sla_id': 1350}))
all_df = pd.DataFrame(all_result)
all_df['ids']

In [20]:
r0 = list(db['exfo_api'].find({'test_status_result': { '$exists': True, '$ne': [] }}).sort("created", -1).limit(10))
r0

AutoReconnect: localhost:27017: connection closed (configured timeouts: connectTimeoutMS: 20000.0ms)

In [18]:
r0 = list(db['exfo_api'].find({'test_status_result': { '$exists': True, '$ne': [] }, 'ids':{'sla_name': {'$regex': '*POC*'}}}).sort("created", -1).limit(10))
r0

[]

In [ ]:
r0 = list(db['exfo_api'].find({'test_status_result': { '$exists': True, '$ne': [] }}).sort("created", -1).limit(10))
pd.json_normalize(r0, ['test_status_result','status', 'results_scores'], ['test_status_result','test_instance_id'], errors='ignore')

In [13]:
from pprint import pprint
list_test_status_result = list(db['exfo_api'].find({'test_status_result': { '$exists': True, '$ne': [] }}, {'test_status_result':1, 'ids': 1}).sort("created", -1).limit(30))
print(len(list_test_status_result))
data = []
data2 = []
for l in list_test_status_result:
    data = data + l['test_status_result']
    data2.append(l['ids'])
print(len(data))
print(len(data2))

30
666
30


In [14]:
df0 = pd.json_normalize(data)
df0
print(len(data))

666


In [15]:
df0['sla_name'].unique()

array(['ATP-Expansion BRIX', 'BV110_NMA', 'BV110_KKN', 'BV110_HYI',
       'BV110_SNI', 'BV1100_BRK', 'BV110_PTY', 'BV110_CMI', 'BV110_NWS',
       'BV110_PLK', 'BV110_RBI'], dtype=object)

In [ ]:
df0['sla_name'].unique()

In [ ]:
len(data2)

In [ ]:
df_ids = pd.json_normalize(data2)
df_ids

In [ ]:
df = pd.json_normalize(data, record_path=['status', 'results_scores'], 
                       meta=['test_instance_id', ['status','time_stamp_display']],  errors='ignore')
df

In [ ]:
df3 = pd.merge(df0, df, on='test_instance_id')
df3

In [ ]:
df3.drop(['status'], axis=1)

In [ ]:
df3.query('test_instance_class_id == 1554')

In [ ]:
ping_test = df3.query("`service.service_name` == 'Ping test'").drop(["status"],axis=1)
ping_test

In [ ]:
ping_test.to_excel("ping_test.xlsx")

In [ ]:
ping_test.dtypes
ping_test.columns

In [ ]:
ping_test["service.service_name"]

In [ ]:
df3['status'][0]

In [ ]:
df3.dtypes

In [ ]:
df3

In [ ]:
df3["value_score"] = df[["raw_value","score"]].astype(str).agg("/".join, axis=1)
df3

In [ ]:
df3

In [ ]:
print(df3.query("sla_name == 'BV110_RBI'"))
print(df3["sla_name"].unique())

In [ ]:
df4 = df3.query("sla_name in ('POC-Expansion-SLA_BRAS_88_Private (VLAN10)','POC-Expansion-SLA_BNG_144_Public (VLAN20)','POC-Expansion-SLA_BNG_144_Private (VLAN10)')")
df4

In [ ]:
df3['sla_name'].unique()

In [ ]:
table = pd.pivot_table(df3, index=['sla_name', 'status.time_stamp_display'], 
                       columns=['service.service_name',  "target.target_value", "name"], values=["raw_value",])
table

In [ ]:
import time
 
# ts stores the time in seconds
ts = int(time.time())
table.to_excel(f"table{ts}.xlsx")

In [ ]:
df3['status'][0]

In [ ]:
df = pd.json_normalize(list_test_status_result, record_path=["test_status_result","status"], meta=[""])
df 

In [ ]:
df.dtypes

In [ ]:
def dict_list_to_df(df, col):
    """Return a Pandas dataframe based on a column that contains a list of JSON objects or dictionaries.
    Args:
        df (Pandas dataframe): The dataframe to be flattened.
        col (str): The name of the column that contains the JSON objects or dictionaries.
    Returns:
        Pandas dataframe: A new dataframe with the JSON objects or dictionaries expanded into columns.
    """

    rows = []
    for index, row in df[col].iteritems():
        for item in row:
            rows.append(item)
    df = pd.DataFrame(rows)
    return df

In [ ]:
df1 = dict_list_to_df(df, "status")
df1

In [ ]:
df2 = dict_list_to_df(df1, "results_scores")
df2

In [ ]:
!pip install flatten-json


In [ ]:
from flatten_json import flatten
df['status_r

In [ ]:
df_flat = pd.io.json.json_normalize(json_struct)
df

In [ ]:
import ast
from pandas.io.json import json_normalize

def only_dict(d):
    '''
    Convert json string representation of dictionary to a python dict
    '''
    return ast.literal_eval(d)

def list_of_dicts(ld):
    '''
    Create a mapping of the tuples formed after 
    converting json strings of list to a python list   
    '''
    return dict([(list(d.values())[1], list(d.values())[0]) for d in ast.literal_eval(ld)])

In [ ]:
A = json_normalize(df['status'].apply(only_dict).tolist()).add_prefix('status.')
A

In [ ]:
pd.json_normalize(list(df['status']))

In [ ]:
new_temp = df.explode('status')
new_temp

In [ ]:
df2 = df.merge(new_temp, left_index=True, right_index=True, suffixes=("_test","_status"))
df2

In [ ]:
df2.to_excel("test.xlsx")

In [ ]:
temp = df.explode('status.results_scores')
temp

In [ ]:
temp

In [ ]:
l1 = []
for l in list_test_status_result:
    l1 = l1 + l['test_status_result']
df = pd.DataFrame(l1)
df = pd.concat([df, df["service"].apply(pd.Series)], axis=1)
df

In [ ]:
df['results_scores']

In [ ]:
import numpy as np

df1 = pd.DataFrame(df['status'][0])
temp_df = pd.DataFrame.from_dict(np.concatenate(df1['results_scores']).tolist())
temp_df[:10]

In [ ]:
final_df = df1.merge(temp_df, how='inner', left_index=True, right_index=True)
final_df


In [ ]:
df = pd.DataFrame(list_test_status_result)
df

In [ ]:
df = df.explode('test_status_result')
df

In [ ]:
l0 = []
for l in list_test_status_result:
    for t in l['test_status_result']:
        for st in t['status']:
            for rs in st['results_scores']:
                temp = t['service'] | (t['target'] or {}) | rs
                temp['sla_name'] = st['sla_name'] 
                temp['time_stamp'] = st['time_stamp']
                temp['time_stamp_display'] = st['time_stamp_display']
                l0.append(temp)
l0[:10]

In [ ]:
list_test_status_result = list(db['exfo_api'].find({}, {'test_status_result':1}))
list_test_status_result

In [ ]:
pd.set_option('display.max_rows', 500)
pd.set_option('display.max_columns', 500)
pd.set_option('display.width', 1000)

temp = []
for l in list_test_status_result:
    for d in l['test_status_result']:
        for s in d['status']:
            for rs in s['results_scores']:
                t2 = {rs['name']: [rs['raw_value'], rs['score']]}
                temp.append({**d, **s, **t2})
temp
df = pd.json_normalize(temp)
#df.set_index(['time_stamp_display'], inplace=True)
df['sla_service'] = df['sla_name'] + "/" + df['service_name']
df['sla_service'].unique()

In [ ]:
f = df[df['sla_service'] == 'BV110_CMI/HTTPS Web Performances']
f.set_index(['time_stamp_display'], inplace=True)
f